# Hints for Session 5

Maybe you find it useful to use my code:

In [1]:
using PyPlot

In [34]:
function binary(z,N)
    x=log(z)/log(2)
    digits=N

    bin_zahl=zeros(Int,digits)
    for i in 1:digits
        rest  =rem(z,2)
        bin_zahl[digits+1-i]=rest
        z=div(z,2)
    end

    return bin_zahl
end

function trafo(x)
    return x-0.5
end

function spin_state_generator(N)
states=Array{Array}(0)                               #empty array
for i in 0:2^N -1                 
    state=trafo(binary(i,N))
    push!(states,state)                    #if possible state has exactly M particles, it is accepted

end
    return states
end



spin_state_generator (generic function with 1 method)

In [35]:
function spinp(i,state)                    #i is site/level/index, state is state in the fock space
                                                          #Important, copy!!! otherwise state array gets changed
    if state[i]==-0.5
        eigenvalue=1
    else
        eigenvalue=0
    end
    
    state[i]=state[i]+1

    return state, eigenvalue
end

spinp (generic function with 1 method)

In [36]:
function spinm(i,state)                    #i is site/level/index, state is state in the fock space
                                                          #Important, copy!!! otherwise state array gets changed
    if state[i]==0.5
        eigenvalue=1
    else
        eigenvalue=0
    end
    
    state[i]=state[i]-1

    return state, eigenvalue
end

spinm (generic function with 1 method)

In [37]:
function spinz(i,state)                    #i is site/level/index, state is state in the fock space
    eigenvalue=state[i]   
    return state, eigenvalue
end

spinz (generic function with 1 method)

In [38]:
function stateprod(state1,state2)
    if state1==state2
        p=1
    else
        p=0
    end
    return p
end

stateprod (generic function with 1 method)

Demonstration <br\>
Say, we have 3 lattice sites and want to calculate the product $\langle \uparrow \uparrow \uparrow | S_1^+ S_2^+ | \downarrow \downarrow \uparrow\rangle$ The procedure is: $S_2^+$ acts on the state $| \downarrow \downarrow \uparrow\rangle$, returning $| \downarrow \uparrow \uparrow\rangle$ and value $e_1=1$ from the operator definition. Then operator $S_1^+$ acts on $| \downarrow \uparrow \uparrow\rangle$ returning state $| \uparrow \uparrow \uparrow\rangle$ with value $e_2$. In the end, we have the product: <br\>
$\langle \uparrow \uparrow \uparrow | \uparrow \uparrow \uparrow\rangle e_1\cdot e_2$. The scalar product of the states with the values results into $1$. <br\>
<br\>
Numerically, this works like this:


In [69]:
states=spin_state_generator(3)   #generate all states for 3 sites
statel=copy(states[8])                 #get the left hand state
stater=copy(states[2])                 #get the right hand state

new_state,e1=spinp(2,stater)     #act S_2^+ on right state
new_state,e2=spinp(1,new_state)  #act S_1^+ on the new right state

result=e1*e2*stateprod(new_state,statel)   #implement product with scalar product 

1

Hint: this implementation avoids the problem, that states getting destroyed. For example $S_1^+ | \uparrow \uparrow \uparrow \rangle$ should vanish. But what instead happens:

In [71]:
stater=copy(states[8])
spinp(1,stater)

([1.5, 0.5, 0.5], 0)

We are getting an unphysical state with a spin of $1.5$ on the first site, but the value is $0$. So the product described in the cell above will automatically return $0$ because of the product of these values.

In [42]:
function H(N,Jx,Jy,Jz)
    sstates=spin_state_generator(N)
    H=zeros(length(sstates),length(sstates))       #Create empty array
    for l in 1:length(sstates)                             #left vector = bra vector
        for r in 1:length(sstates)                         #right vector = ket vector
            h=0
            stateL=copy(sstates[l])
            

            for j in 1:N
                for i in 1:N                                    #perform operators
                    stateR=copy(sstates[r])                        #Again: copy state
                    s1,ew1=spinp(j,stateR)
                    s2,ew2=spinp(i,s1)
                    p=stateprod(s2,stateL)
                    h=h+(-p*ew1*ew2*(Jx[i,j]-Jy[i,j]))/4

                    stateR=copy(sstates[r])                        #Again: copy state
                    s1,ew1=spinm(j,stateR)
                    s2,ew2=spinm(i,s1)
                    p=stateprod(s2,stateL)
                    h=h+(-p*ew1*ew2*(Jx[i,j]-Jy[i,j]))/4

                    stateR=copy(sstates[r])                        #Again: copy state
                    s1,ew1=spinm(j,stateR)
                    s2,ew2=spinp(i,s1)
                    p=stateprod(s2,stateL)
                    h=h+(-p*ew1*ew2*(Jx[i,j]+Jy[i,j]))/4

                    stateR=copy(sstates[r])                        #Again: copy state
                    s1,ew1=spinp(j,stateR)
                    s2,ew2=spinm(i,s1)
                    p=stateprod(s2,stateL)
                    h=h+(-p*ew1*ew2*(Jx[i,j]+Jy[i,j]))/4

                    stateR=copy(sstates[r])                        #Again: copy state
                    s1,ew1=spinz(j,stateR)
                    s2,ew2=spinz(i,s1)
                    p=stateprod(s2,stateL)
                    h=h+(-p*ew1*ew2*Jz[i,j])
                end
            end

            
            H[l,r]=h                                      #fill matrix
        end
    end
    return H
end


H (generic function with 1 method)

Example: 1d Ising Chain with N lattice sites

In [43]:
N=8

Jx=zeros(N,N)
Jy=zeros(N,N)
Jz=zeros(N,N)

Jx[1,2]=0
Jx[2,3]=0
Jx[3,4]=0
Jx[4,5]=0
Jx[5,6]=0
Jx[6,7]=0
Jx[7,8]=0

Jy[1,2]=0
Jy[2,3]=0
Jy[3,4]=0
Jy[4,5]=0
Jy[5,6]=0
Jy[6,7]=0
Jy[7,8]=0

Jz[1,2]=1
Jz[2,3]=1
Jz[3,1]=1
Jz[3,4]=1
Jz[4,5]=1
Jz[5,6]=1
Jz[6,7]=1
Jz[7,8]=1


hamilton=H(4,Jx,Jy,Jz)

16×16 Array{Float64,2}:
 -1.0   0.0  0.0  0.0  0.0  0.0  0.0  …  0.0  0.0  0.0  0.0  0.0   0.0   0.0
  0.0  -0.5  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0   0.0   0.0
  0.0   0.0  0.5  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0   0.0   0.0
  0.0   0.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0   0.0   0.0
  0.0   0.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0   0.0   0.0
  0.0   0.0  0.0  0.0  0.0  0.5  0.0  …  0.0  0.0  0.0  0.0  0.0   0.0   0.0
  0.0   0.0  0.0  0.0  0.0  0.0  0.5     0.0  0.0  0.0  0.0  0.0   0.0   0.0
  0.0   0.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0   0.0   0.0
  0.0   0.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0   0.0   0.0
  0.0   0.0  0.0  0.0  0.0  0.0  0.0     0.5  0.0  0.0  0.0  0.0   0.0   0.0
  0.0   0.0  0.0  0.0  0.0  0.0  0.0  …  0.0  0.5  0.0  0.0  0.0   0.0   0.0
  0.0   0.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0.0  0.0  0.0   0.0   0.0
  0.0   0.0  0.0  0.0  0.0  0.0  0.0     0.0  0.0  0

In [46]:
groundstate=eigvecs(hamilton)[:,1]

16-element Array{Float64,1}:
 1.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0
 0.0

# Correlation

$C_{l,m}=\langle{\psi_g}| \vec{S}_l \cdot \vec{S}_m | \psi_g \rangle 
= \langle{\psi_g}| \ \frac{1}{2} \ S^{+}_{l}S^{-}_{m} + \ \frac{1}{2} \ S^{-}_{l}S^{+}_{m} + S^{z}_{l}S^{z}_{m} \ | \psi_g \rangle $

Important: the groundstate extractet from the Hamilton matrix has the following form:

$| \psi_g \rangle = a_0 |0 \rangle + a_1 |1\rangle + \dots + a_{15} |15\rangle   $

Therefore, the correlation becomes the sum of many products:

$C_{l,m}=\left( a_0 \langle 0 |  + a_1 \langle 1 | + \dots + a_{15} \langle 15 | \right) \left( \frac{1}{2} \ S^{+}_{l}S^{-}_{m} + \ \frac{1}{2} \ S^{-}_{l}S^{+}_{m} + S^{z}_{l}S^{z}_{m}\right)\left(a_0 |0 \rangle + a_1 |1\rangle + \dots + a_{15} |15\rangle \right)$

$C_{l,m}= a_0a_0 \langle 0 | \left( \frac{1}{2} \ S^{+}_{l}S^{-}_{m} + \ \frac{1}{2} \ S^{-}_{l}S^{+}_{m} + S^{z}_{l}S^{z}_{m}\right) |0\rangle + a_0a_1 \langle 0 | \left( \frac{1}{2} \ S^{+}_{l}S^{-}_{m} + \ \frac{1}{2} \ S^{-}_{l}S^{+}_{m} + S^{z}_{l}S^{z}_{m}\right) |1\rangle + \dots a_0a_{15} \langle 0 | \left( \frac{1}{2} \ S^{+}_{l}S^{-}_{m} + \ \frac{1}{2} \ S^{-}_{l}S^{+}_{m} + S^{z}_{l}S^{z}_{m}\right) |15\rangle + a_1a_0 \langle 1 | \left( \frac{1}{2} \ S^{+}_{l}S^{-}_{m} + \ \frac{1}{2} \ S^{-}_{l}S^{+}_{m} + S^{z}_{l}S^{z}_{m}\right) |0\rangle + \dots + a_{15}a_{15} \langle 15 | \left( \frac{1}{2} \ S^{+}_{l}S^{-}_{m} + \ \frac{1}{2} \ S^{-}_{l}S^{+}_{m} + S^{z}_{l}S^{z}_{m}\right) |15\rangle$

Therefore it is useful to implement two  functions:

$singlecorrelation(stater,statel,l,m)$, which takes two states (stater,statel) and calculates the product $\langle \psi_l | \left( \frac{1}{2} \ S^{+}_{l}S^{-}_{m} + \ \frac{1}{2} \ S^{-}_{l}S^{+}_{m} + S^{z}_{l}S^{z}_{m}\right) |\psi_r \rangle$

$correlation(state,l,m,N)$, takes the groundstate $state$ with of a $N$-site model and calculates the whole correlation by summing up the terms given via the $singlecorrelation$ function.